In [6]:
import os
import string
import numpy as np
import pandas as pd
import nltk
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from sklearn.svm import LinearSVC
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score, classification_report, confusion_matrix
import spacy
from spacy.lang.en.stop_words import STOP_WORDS
import joblib
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize

In [10]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\Glenn\AppData\Roaming\nltk_data...
[nltk_data]   Unzipping tokenizers\punkt.zip.


True

In [2]:
df = pd.read_excel("bw_reviews.xlsx", "reviews")

In [3]:
df.head()

Content  Score
0  Easy to order but despatch and delivery to Can...      4
1  Quick process of orders. Very good prices comp...      5
2  So far it's been quick and easy to order.  Wil...      5
3  Very easy to navigate site, easy to order from...      5
4  I am upgrading my original review to 4 stars. ...      4

In [4]:
df['Score'].value_counts()

Score
5    8417
4     691
1     449
3     284
2     159
Name: count, dtype: int64

In [15]:
def text_cleaning(content):
    stop_words = set(stopwords.words('english'))

    punct = string.punctuation

    word_tokens = word_tokenize(content)
    filtered = []

    for w in word_tokens:
        if w not in stop_words and w not in punct:
            filtered.append(w)
            
    return filtered

In [16]:
new_frame = pd.DataFrame(columns = ['Content', 'Score'])

In [17]:
for _, row in df.iterrows():
    filtered_tokens = text_cleaning(row['Content'])
    new_row = pd.DataFrame([[filtered_tokens, row['Score']]], columns = ['Content', 'Score'])
    new_frame = pd.concat([new_frame, new_row])
    print(new_frame)

                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
0  [Quick, process, orders, Very, good, prices, c...     5
                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
0  [Quick, process, orders, Very, good, prices, c...     5
0  [So, far, 's, quick, easy, order, Will, wait, ...     5
                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
0  [Quick, process, orders, Very, good, prices, c...     5
0  [So, far, 's, quick, easy, order, Will, wait, ...     5
0  [Very, easy, navigate, site, easy, order, Cana...     5
                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
0  [Quick, process, orders, Very, good, prices, c...    

                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
0  [Quick, process, orders, Very, good, prices, c...     5
0  [So, far, 's, quick, easy, order, Will, wait, ...     5
0  [Very, easy, navigate, site, easy, order, Cana...     5
0  [I, upgrading, original, review, 4, stars, I, ...     4
0  [This, second, time, I, found, books, I, unabl...     5
0  [Easy, order, delivery, Canada, quite, fast, C...     5
0  [I, grabbed, two, copies, Iron, Flame, Fourth,...     5
0  [Excellent, range, books, clearly, set, explan...     5
0  [A, great, selection, books, offers, Beautiful...     5
0  [Checkout, quick, straightforward, I, managed,...     5
0  [All, books, arrived, safely, swiftly, There, ...     5
0  [Thank, much, I, definitely, recommending, web...     5
0  [Great, UX, store, It, easy, navigate, worked,...     5
0  [I, order, use, Blackwells, rather, main, book...     5
0  [Blackwell, efficient, provides, great, readin...    

                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
0  [Quick, process, orders, Very, good, prices, c...     5
0  [So, far, 's, quick, easy, order, Will, wait, ...     5
0  [Very, easy, navigate, site, easy, order, Cana...     5
0  [I, upgrading, original, review, 4, stars, I, ...     4
0  [This, second, time, I, found, books, I, unabl...     5
0  [Easy, order, delivery, Canada, quite, fast, C...     5
0  [I, grabbed, two, copies, Iron, Flame, Fourth,...     5
0  [Excellent, range, books, clearly, set, explan...     5
0  [A, great, selection, books, offers, Beautiful...     5
0  [Checkout, quick, straightforward, I, managed,...     5
0  [All, books, arrived, safely, swiftly, There, ...     5
0  [Thank, much, I, definitely, recommending, web...     5
0  [Great, UX, store, It, easy, navigate, worked,...     5
0  [I, order, use, Blackwells, rather, main, book...     5
0  [Blackwell, efficient, provides, great, readin...    

                                             Content Score
0  [Easy, order, despatch, delivery, Canada, took...     4
0  [Quick, process, orders, Very, good, prices, c...     5
0  [So, far, 's, quick, easy, order, Will, wait, ...     5
0  [Very, easy, navigate, site, easy, order, Cana...     5
0  [I, upgrading, original, review, 4, stars, I, ...     4
0  [This, second, time, I, found, books, I, unabl...     5
0  [Easy, order, delivery, Canada, quite, fast, C...     5
0  [I, grabbed, two, copies, Iron, Flame, Fourth,...     5
0  [Excellent, range, books, clearly, set, explan...     5
0  [A, great, selection, books, offers, Beautiful...     5
0  [Checkout, quick, straightforward, I, managed,...     5
0  [All, books, arrived, safely, swiftly, There, ...     5
0  [Thank, much, I, definitely, recommending, web...     5
0  [Great, UX, store, It, easy, navigate, worked,...     5
0  [I, order, use, Blackwells, rather, main, book...     5
0  [Blackwell, efficient, provides, great, readin...    

                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy, navigate, site, easy, order, Cana...     5
0   [I, upgrading, original, review, 4, stars, I, ...     4
..                                                ...   ...
0   [Could, find, books, anywhere, else, delivered...     5
0   [Always, great, experience, especially, I, liv...     5
0   [Easy, use, I, hopeful, shipping/delivery, exp...     5
0   [The, availability, ease, ordering, course, pr...     5
0   [I, found, book, I, wanted, quickly, competiti...     5

[71 rows x 2 columns]
                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy, 

...

                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy, navigate, site, easy, order, Cana...     5
0   [I, upgrading, original, review, 4, stars, I, ...     4
..                                                ...   ...
0   [Ran, stock, ’, update, They, waited, I, email...     1
0   [When, I, ticked, I, 'd, forgotten, password, ...     5
0   [I, love, selection, books, site, user, friend...     5
0               [The, ordering, process, quick, easy]     5
0               [Quick, good, guidance, orderprocess]     5

[9835 rows x 2 columns]
                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy

                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy, navigate, site, easy, order, Cana...     5
0   [I, upgrading, original, review, 4, stars, I, ...     4
..                                                ...   ...
0                                 [Super, efficiency]     5
0                                   [Swift, delivery]     5
0   [Always, good, choices, swift, service, great,...     5
0   [Ordering, easy, It, 's, first, time, ordering...     5
0   [This, tiny, order, £5, quite, obscure, title,...     5

[9873 rows x 2 columns]
                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy

                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy, navigate, site, easy, order, Cana...     5
0   [I, upgrading, original, review, 4, stars, I, ...     4
..                                                ...   ...
0   [My, order, came, quicker, I, thought, great, ...     5
0                                   [Fast, easy, buy]     5
0   [The, book, still, arrived, 3, weeks, 2-4, day...     1
0    [Good, price, ordering, website, easy, navigate]     5
0   [Reasonable, price, Good, interface, Not, Amazon]     5

[9913 rows x 2 columns]
                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy

                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy, navigate, site, easy, order, Cana...     5
0   [I, upgrading, original, review, 4, stars, I, ...     4
..                                                ...   ...
0                              [site, easy, navigate]     5
0   [Easy, site, use, Ordering, straight, forward,...     5
0   [Blackwells, enormous, online, library, They, ...     5
0   [The, cheapest, price, I, could, find, online,...     5
0   [Very, good, choice, books, reasonable, prices...     5

[9954 rows x 2 columns]
                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy

                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy, navigate, site, easy, order, Cana...     5
0   [I, upgrading, original, review, 4, stars, I, ...     4
..                                                ...   ...
0                      [Delivered, time, good, price]     5
0   [Easy, order, books, great, price, free, deliv...     5
0        [Very, easy, quick, system, complete, order]     5
0   [Clean, easy, navigate, website, And, besides,...     5
0   [I, turned, traders, easier, friendlier, deal,...     5

[9993 rows x 2 columns]
                                              Content Score
0   [Easy, order, despatch, delivery, Canada, took...     4
0   [Quick, process, orders, Very, good, prices, c...     5
0   [So, far, 's, quick, easy, order, Will, wait, ...     5
0   [Very, easy

In [35]:
words = pd.concat([pd.Series(row['Score'], row['Content'])            
    for _, row in new_frame.iterrows()]).reset_index()
words.columns = ['word', 'score']
grouped = words.groupby(['score', 'word']).size().reset_index()
grouped.columns = ['score', 'word', 'count']
print(grouped)

with pd.ExcelWriter("sentiment_count.xlsx", engine="xlsxwriter") as writer:
    grouped.to_excel(writer, sheet_name="count")

       score         word  count
0          1           ''     20
1          1           'd      7
2          1    'delivery      1
3          1  'despatched      1
4          1  'dispatched      1
...      ...          ...    ...
15985      5            🤞      1
15986      5            🤩      2
15987      5   🥇wonderful      1
15988      5           🥹🥹      1
15989      5            🩷      1

[15990 rows x 3 columns]


In [5]:
x = df['Content']
y = df['Score']

In [6]:
score_list = []
for i in y:
    score = i - 1
    score_list.append(score)
score_list = np.asarray(score_list)
score_list = to_categorical(score_list, num_classes=5)
print(score_list)

[[0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 1.]
 ...
 [0. 0. 0. 1. 0.]
 [0. 0. 0. 0. 1.]
 [0. 0. 0. 0. 1.]]


In [7]:
punct = string.punctuation
punct

stopwords = list(STOP_WORDS)

In [8]:
nlp = spacy.load('en_core_web_sm')
def text_cleaning(content):
    doc = nlp(content)
    
    tokens = []
    for token in doc:
        if token.lemma != "-PRON-":
            temp = token.lemma_.lower().strip()
        else:
            temp = token.lower_
        tokens.append(temp)
        
    cleaned_tokens = []
    for token in tokens:
        if token not in stopwords and token not in punct:
            cleaned_tokens.append(token)
    return cleaned_tokens

In [9]:
tfidf = TfidfVectorizer(tokenizer=text_cleaning)

In [10]:
classifier = LinearSVC()

In [11]:
from sklearn.model_selection import train_test_split
x_train, x_test, y_train, y_test = train_test_split(x, y, test_size=0.2)

In [12]:
clf = Pipeline([('tfidf', tfidf), ('clf',classifier)])

In [13]:
clf.fit(x_train, y_train)

C:\Python311\Lib\site-packages\sklearn\feature_extraction\text.py:525: UserWarning: The parameter 'token_pattern' will not be used since 'tokenizer' is not None'
  warnings.warn(
C:\Python311\Lib\site-packages\sklearn\svm\_classes.py:32: FutureWarning: The default value of `dual` will change from `True` to `'auto'` in 1.5. Set the value of `dual` explicitly to suppress the warning.
  warnings.warn(


Pipeline(steps=[('tfidf',
                 TfidfVectorizer(tokenizer=<function text_cleaning at 0x00000173EA0E6E80>)),
                ('clf', LinearSVC())])

In [14]:
y_pred = clf.predict(x_test)

In [15]:
print(classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           1       0.56      0.54      0.55        92
           2       0.00      0.00      0.00        29
           3       0.23      0.17      0.19        54
           4       0.27      0.08      0.12       132
           5       0.91      0.98      0.94      1693

    accuracy                           0.86      2000
   macro avg       0.39      0.35      0.36      2000
weighted avg       0.82      0.86      0.84      2000



In [16]:
accuracy_score(y_test, y_pred)

0.864

In [17]:
#Rating 5
clf.predict(["Good service, great prices, smooth transaction and great delivery time"])

array([5], dtype=int64)

In [18]:
#Rating 4
clf.predict(["Could be better, delivery time took a little longer but product was in good condition"])

array([4], dtype=int64)

In [19]:
#Rating 3
clf.predict(["Nothing too great about their services. I have seen other sites with similar prices and delivery time. Overall not too bad"])

array([5], dtype=int64)

In [20]:
#Rating 2
clf.predict(["Product arrived in a pretty bad condition, tried asking for a new product or a refund but got no response instead"])

array([5], dtype=int64)

In [21]:
#Rating 1
clf.predict(["Service was horrible, paid for an item and have been waiting for months, did not get any response from them"])

array([1], dtype=int64)

In [22]:
filename = 'sa.model'
joblib.dump(clf, filename)

['sa.model']